In [32]:
import pandas as pd
import polars as pl
import numpy as np
import datetime as dt
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import mplfinance as mpf
from plotly.subplots import make_subplots
from dash import Dash, dcc, html
import pandas_market_calendars as mcal
nse = mcal.get_calendar('NSE')

In [33]:
pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)

polars.config.Config

In [34]:
import sys
sys.path.append('..')
from tooling.filter import find_atm, option_tool
from tooling.fetch import fetch_option_data, fetch_spot_data
from tooling.filter import find_atm
from tooling.enums import Index, AssetClass, StrikeSpread, Spot

In [35]:
def get_expiry(f_today):
    days_to_thursday = (3 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry

def get_option_contract_name(symbol, strike, expiry, opt_type):
    temp = '0'
    mth=expiry.month

    if (expiry + dt.timedelta(days=7)).month != expiry.month:
        date_string = expiry.strftime('%y%b').upper()
        return f'{symbol}{date_string}{strike}{opt_type}'
    else:
        if expiry.day<=9:
            date_string = f'{expiry.year - 2000}{mth}{temp}{expiry.day}'
        else :
            date_string = f'{expiry.year - 2000}{mth}{expiry.day}'
        return f'{symbol}{date_string}{strike}{opt_type}'

In [36]:
# bnf = pd.read_csv('../data/bnf_min.csv')
bnf_pandas = pd.read_csv('../data/gold_4hr.csv')

In [37]:
bnf_pandas

time   open   high    low  close  Volume
0     2015-03-02T09:00:00+05:30  26600  26769  26600  26700    2387
1     2015-03-02T13:00:00+05:30  26709  26730  26653  26680    2104
2     2015-03-02T17:00:00+05:30  26684  26742  26576  26619    2285
3     2015-03-02T21:00:00+05:30  26623  26624  26500  26506    1796
4     2015-03-03T09:00:00+05:30  26500  26525  26444  26463    1800
5     2015-03-03T13:00:00+05:30  26470  26533  26453  26498    1495
6     2015-03-03T17:00:00+05:30  26499  26590  26437  26550    2672
7     2015-03-03T21:00:00+05:30  26548  26566  26380  26440    2149
8     2015-03-04T09:00:00+05:30  26411  26475  26409  26439    1465
9     2015-03-04T13:00:00+05:30  26438  26560  26415  26537    2850
10    2015-03-04T17:00:00+05:30  26540  26579  26480  26525    2341
11    2015-03-04T21:00:00+05:30  26524  26568  26502  26535    1844
12    2015-03-05T09:00:00+05:30  26565  26579  26475  26480    1725
13    2015-03-05T13:00:00+05:30  26484  26499  26435  26453    1641
14    2015-03-05T17:00:00+05:30  26453  26586  26450  26574    1624
15    2015-03-05T21:00:00+05:30  26576  26627  26462  26475    1835
16    2015-03-06T17:00:00+05:30  26460  26484  26170  26200    3683
17    2015-03-06T21:00:00+05:30  26200  26235  25982  25987    2482
18    2015-03-09T09:00:00+05:30  26073  26096  26036  26063    1803
19    2015-03-09T13:00:00+05:30  26062  26125  26056  26076    2194
20    2015-03-09T17:00:00+05:30  26075  26129  26006  26027    2243
21    2015-03-09T21:00:00+05:30  26027  26045  26001  26022    1418
22    2015-03-10T09:00:00+05:30  25962  25962  25825  25861    3078
23    2015-03-10T13:00:00+05:30  25860  25950  25780  25943    3328
24    2015-03-10T17:00:00+05:30  25944  26079  25894  25937    3691
25    2015-03-10T21:00:00+05:30  25935  25975  25873  25916    1862
26    2015-03-11T09:00:00+05:30  25950  25950  25885  25925    1925
27    2015-03-11T13:00:00+05:30  25921  25934  25821  25882    2765
28    2015-03-11T17:00:00+05:30  25878  25883  25653  25704    3878
29    2015-03-11T21:00:00+05:30  25708  25750  25660  25685    1977
30    2015-03-12T09:00:00+05:30  25660  25860  25626  25809    3670
31    2015-03-12T13:00:00+05:30  25810  25812  25732  25745    2830
32    2015-03-12T17:00:00+05:30  25746  25759  25615  25643    3401
33    2015-03-12T21:00:00+05:30  25646  25669  25562  25648    2001
34    2015-03-13T09:00:00+05:30  25720  25846  25720  25787    2507
35    2015-03-13T13:00:00+05:30  25788  25872  25761  25841    2834
36    2015-03-13T17:00:00+05:30  25840  25918  25785  25798    3179
37    2015-03-13T21:00:00+05:30  25810  25915  25800  25912    1935
38    2015-03-16T09:00:00+05:30  25875  25941  25860  25908    1692
39    2015-03-16T13:00:00+05:30  25909  25910  25780  25790    1932
40    2015-03-16T17:00:00+05:30  25791  25850  25706  25739    2503
41    2015-03-16T21:00:00+05:30  25739  25796  25725  25775    1811
42    2015-03-17T09:00:00+05:30  25721  25749  25687  25735    1648
43    2015-03-17T13:00:00+05:30  25732  25738  25676  25692    2100
44    2015-03-17T17:00:00+05:30  25688  25830  25521  25660    4704
45    2015-03-17T21:00:00+05:30  25663  25680  25592  25619    1740
46    2015-03-18T09:00:00+05:30  25631  25650  25500  25508    2761
47    2015-03-18T13:00:00+05:30  25508  25670  25501  25620    2805
48    2015-03-18T17:00:00+05:30  25619  25648  25555  25632    1982
49    2015-03-18T21:00:00+05:30  25637  25697  25612  25647    1759
50    2015-03-19T09:00:00+05:30  25740  25946  25740  25920    2965
51    2015-03-19T13:00:00+05:30  25918  25925  25826  25842    2889
52    2015-03-19T17:00:00+05:30  25845  25919  25774  25903    2790
53    2015-03-19T21:00:00+05:30  25897  25997  25893  25956    2013
54    2015-03-20T09:00:00+05:30  25980  25990  25906  25968    2055
55    2015-03-20T13:00:00+05:30  25965  26020  25900  25978    1866
56    2015-03-20T17:00:00+05:30  25979  26157  25909  26108    3313
57    2015-03-20T21:00:00+05:30  26110  26236  26105  26170    2195
58    2015-03-2

In [38]:
# If Stocks Data ...
bnf_pandas['datetime'] = pd.to_datetime(bnf_pandas['time'])
bnf_pandas['datetime'] = bnf_pandas['datetime'].dt.tz_localize(None)
bnf_pandas.drop(columns=['time'], inplace=True)
# bnf_pandas

In [39]:
bnf = pl.DataFrame(bnf_pandas)
print(type(bnf))
bnf

<class 'polars.dataframe.frame.DataFrame'>


shape: (9_044, 6)
┌───────┬───────┬───────┬───────┬────────┬─────────────────────┐
│ open  ┆ high  ┆ low   ┆ close ┆ Volume ┆ datetime            │
│ ---   ┆ ---   ┆ ---   ┆ ---   ┆ ---    ┆ ---                 │
│ i64   ┆ i64   ┆ i64   ┆ i64   ┆ i64    ┆ datetime[ns]        │
╞═══════╪═══════╪═══════╪═══════╪════════╪═════════════════════╡
│ 26600 ┆ 26769 ┆ 26600 ┆ 26700 ┆ 2387   ┆ 2015-03-02 09:00:00 │
│ 26709 ┆ 26730 ┆ 26653 ┆ 26680 ┆ 2104   ┆ 2015-03-02 13:00:00 │
│ 26684 ┆ 26742 ┆ 26576 ┆ 26619 ┆ 2285   ┆ 2015-03-02 17:00:00 │
│ 26623 ┆ 26624 ┆ 26500 ┆ 26506 ┆ 1796   ┆ 2015-03-02 21:00:00 │
│ 26500 ┆ 26525 ┆ 26444 ┆ 26463 ┆ 1800   ┆ 2015-03-03 09:00:00 │
│ 26470 ┆ 26533 ┆ 26453 ┆ 26498 ┆ 1495   ┆ 2015-03-03 13:00:00 │
│ 26499 ┆ 26590 ┆ 26437 ┆ 26550 ┆ 2672   ┆ 2015-03-03 17:00:00 │
│ 26548 ┆ 26566 ┆ 26380 ┆ 26440 ┆ 2149   ┆ 2015-03-03 21:00:00 │
│ 26411 ┆ 26475 ┆ 26409 ┆ 26439 ┆ 1465   ┆ 2015-03-04 09:00:00 │
│ 26438 ┆ 26560 ┆ 26415 ┆ 26537 ┆ 2850   ┆ 2015-03-04 13:00:00 │
│ 26540 ┆ 26579 ┆ 26480 ┆ 26525 ┆ 2341   ┆ 2015-03-04 17:00:00 │
│ 26524 ┆ 26568 ┆ 26502 ┆ 26535 ┆ 1844   ┆ 2015-03-04 21:00:00 │
│ 26565 ┆ 26579 ┆ 26475 ┆ 26480 ┆ 1725   ┆ 2015-03-05 09:00:00 │
│ 26484 ┆ 26499 ┆ 26435 ┆ 26453 ┆ 1641   ┆ 2015-03-05 13:00:00 │
│ 26453 ┆ 26586 ┆ 26450 ┆ 26574 ┆ 1624   ┆ 2015-03-05 17:00:00 │
│ 26576 ┆ 26627 ┆ 26462 ┆ 26475 ┆ 1835   ┆ 2015-03-05 21:00:00 │
│ 26460 ┆ 26484 ┆ 26170 ┆ 26200 ┆ 3683   ┆ 2015-03-06 17:00:00 │
│ 26200 ┆ 26235 ┆ 25982 ┆ 25987 ┆ 2482   ┆ 2015-03-06 21:00:00 │
│ 26073 ┆ 26096 ┆ 26036 ┆ 26063 ┆ 1803   ┆ 2015-03-09 09:00:00 │
│ 26062 ┆ 26125 ┆ 26056 ┆ 26076 ┆ 2194   ┆ 2015-03-09 13:00:00 │
│ 26075 ┆ 26129 ┆ 26006 ┆ 26027 ┆ 2243   ┆ 2015-03-09 17:00:00 │
│ 26027 ┆ 26045 ┆ 26001 ┆ 26022 ┆ 1418   ┆ 2015-03-09 21:00:00 │
│ 25962 ┆ 25962 ┆ 25825 ┆ 25861 ┆ 3078   ┆ 2015-03-10 09:00:00 │
│ 25860 ┆ 25950 ┆ 25780 ┆ 25943 ┆ 3328   ┆ 2015-03-10 13:00:00 │
│ 25944 ┆ 26079 ┆ 25894 ┆ 25937 ┆ 3691   ┆ 2015-03-10 17:00:00 │
│ 25935 ┆ 25975 ┆ 25873 ┆ 25916 ┆ 1862   ┆ 2015-03-10 21:00:00 │
│ 25950 ┆ 25950 ┆ 25885 ┆ 25925 ┆ 1925   ┆ 2015-03-11 09:00:00 │
│ 25921 ┆ 25934 ┆ 25821 ┆ 25882 ┆ 2765   ┆ 2015-03-11 13:00:00 │
│ 25878 ┆ 25883 ┆ 25653 ┆ 25704 ┆ 3878   ┆ 2015-03-11 17:00:00 │
│ 25708 ┆ 25750 ┆ 25660 ┆ 25685 ┆ 1977   ┆ 2015-03-11 21:00:00 │
│ 25660 ┆ 25860 ┆ 25626 ┆ 25809 ┆ 3670   ┆ 2015-03-12 09:00:00 │
│ 25810 ┆ 25812 ┆ 25732 ┆ 25745 ┆ 2830   ┆ 2015-03-12 13:00:00 │
│ 25746 ┆ 25759 ┆ 25615 ┆ 25643 ┆ 3401   ┆ 2015-03-12 17:00:00 │
│ 25646 ┆ 25669 ┆ 25562 ┆ 25648 ┆ 2001   ┆ 2015-03-12 21:00:00 │
│ 25720 ┆ 25846 ┆ 25720 ┆ 25787 ┆ 2507   ┆ 2015-03-13 09:00:00 │
│ 25788 ┆ 25872 ┆ 25761 ┆ 25841 ┆ 2834   ┆ 2015-03-13 13:00:00 │
│ 25840 ┆ 25918 ┆ 25785 ┆ 25798 ┆ 3179   ┆ 2015-03-13 17:00:00 │
│ 25810 ┆ 25915 ┆ 25800 ┆ 25912 ┆ 1935   ┆ 2015-03-13 21:00:00 │
│ 25875 ┆ 25941 ┆ 25860 ┆ 25908 ┆ 1692   ┆ 2015-03-16 09:00:00 │
│ 25909 ┆ 25910 ┆ 25780 ┆ 25790 ┆ 1932   ┆ 2015-03-16 13:00:00 │
│ 25791 ┆ 25850 ┆ 25706 ┆ 25739 ┆ 2503   ┆ 2015-03-16 17:00:00 │
│ 25739 ┆ 25796 ┆ 25725 ┆ 25775 ┆ 1811   ┆ 2015-03-16 21:00:00 │
│ 25721 ┆ 25749 ┆ 25687 ┆ 25735 ┆ 1648   ┆ 2015-03-17 09:00:00 │
│ 25732 ┆ 25738 ┆ 25676 ┆ 25692 ┆ 2100   ┆ 2015-03-17 13:00:00 │
│ 25688 ┆ 25830 ┆ 25521 ┆ 25660 ┆ 4704   ┆ 2015-03-17 17:00:00 │
│ 25663 ┆ 25680 ┆ 25592 ┆ 25619 ┆ 1740   ┆ 2015-03-17 21:00:00 │
│ 25631 ┆ 25650 ┆ 25500 ┆ 25508 ┆ 2761   ┆ 2015-03-18 09:00:00 │
│ 25508 ┆ 25670 ┆ 25501 ┆ 25620 ┆ 2805   ┆ 2015-03-18 13:00:00 │
│ 25619 ┆ 25648 ┆ 25555 ┆ 25632 ┆ 1982   ┆ 2015-03-18 17:00:00 │
│ 25637 ┆ 25697 ┆ 25612 ┆ 25647 ┆ 1759   ┆ 2015-03-18 21:00:00 │
│ 25740 ┆ 25946 ┆ 25740 ┆ 25920 ┆ 2965   ┆ 2015-03-19 09:00:00 │
│ 25918 ┆ 25925 ┆ 25826 ┆ 25842 ┆ 2889   ┆ 2015-03-19 13:00:00 │
│ 25845 ┆ 25919 ┆ 25774 ┆ 25903 ┆ 2790   ┆ 2015-03-19 17:00:00 │
│ 25897 ┆ 25997 ┆ 25893 ┆ 25956 ┆ 2013   ┆ 2015-03-19 21:00:00 │
│ 25980 ┆ 25990 ┆ 25906 ┆ 25968 ┆ 2055   ┆ 2015-03-20 09:00:00 │
│ 25965 ┆ 26020 ┆ 25900 ┆ 25978 ┆ 1866   ┆ 2015-03-20 13:00:00 │
│ 25979 ┆ 26157 ┆

In [1209]:
# For crude oil Data
bnf1 = pd.DataFrame(bnf_pandas)
bnf1 = bnf1.drop(columns=['Unnamed: 0', 'Unnamed: 0.1'])
bnf1['datetime'] = pd.to_datetime(bnf1['datetime'])
bnf1['index'] = bnf1['datetime']
bnf1.rename(columns={'o': 'open', 'h': 'high', 'l': 'low', 'c': 'close'}, inplace=True)
bnf = pl.DataFrame(bnf1)
print(type(bnf))
bnf

KeyError: "['Unnamed: 0', 'Unnamed: 0.1'] not found in axis"

In [40]:
# bnf['datetime'] = pd.to_datetime(bnf['datetime'])
# bnf = bnf.drop(columns=['Unnamed: 0'])
# bnf.set_index(bnf['datetime'], inplace=True)
# bnf
# bnf = bnf.with_columns(pl.col('datetime').str.to_datetime(format='%Y-%m-%dT%H:%M:%S.%f'))
# print(bnf)
# bnf = bnf.with_columns(pl.col('datetime').cast(pl.DateTime))

# Set 'datetime' column as index
bnf = bnf.with_columns([pl.col('datetime').alias('index')]).drop('datetime')

# Now 'datetime' is set as the index
# bnf

In [41]:
bnf = bnf.with_columns(pl.col("index").alias("datetime"))
# bnf

In [42]:
bnf

shape: (9_044, 7)
┌───────┬───────┬───────┬───────┬────────┬─────────────────────┬─────────────────────┐
│ open  ┆ high  ┆ low   ┆ close ┆ Volume ┆ index               ┆ datetime            │
│ ---   ┆ ---   ┆ ---   ┆ ---   ┆ ---    ┆ ---                 ┆ ---                 │
│ i64   ┆ i64   ┆ i64   ┆ i64   ┆ i64    ┆ datetime[ns]        ┆ datetime[ns]        │
╞═══════╪═══════╪═══════╪═══════╪════════╪═════════════════════╪═════════════════════╡
│ 26600 ┆ 26769 ┆ 26600 ┆ 26700 ┆ 2387   ┆ 2015-03-02 09:00:00 ┆ 2015-03-02 09:00:00 │
│ 26709 ┆ 26730 ┆ 26653 ┆ 26680 ┆ 2104   ┆ 2015-03-02 13:00:00 ┆ 2015-03-02 13:00:00 │
│ 26684 ┆ 26742 ┆ 26576 ┆ 26619 ┆ 2285   ┆ 2015-03-02 17:00:00 ┆ 2015-03-02 17:00:00 │
│ 26623 ┆ 26624 ┆ 26500 ┆ 26506 ┆ 1796   ┆ 2015-03-02 21:00:00 ┆ 2015-03-02 21:00:00 │
│ 26500 ┆ 26525 ┆ 26444 ┆ 26463 ┆ 1800   ┆ 2015-03-03 09:00:00 ┆ 2015-03-03 09:00:00 │
│ 26470 ┆ 26533 ┆ 26453 ┆ 26498 ┆ 1495   ┆ 2015-03-03 13:00:00 ┆ 2015-03-03 13:00:00 │
│ 26499 ┆ 26590 ┆ 26437 ┆ 26550 ┆ 2672   ┆ 2015-03-03 17:00:00 ┆ 2015-03-03 17:00:00 │
│ 26548 ┆ 26566 ┆ 26380 ┆ 26440 ┆ 2149   ┆ 2015-03-03 21:00:00 ┆ 2015-03-03 21:00:00 │
│ 26411 ┆ 26475 ┆ 26409 ┆ 26439 ┆ 1465   ┆ 2015-03-04 09:00:00 ┆ 2015-03-04 09:00:00 │
│ 26438 ┆ 26560 ┆ 26415 ┆ 26537 ┆ 2850   ┆ 2015-03-04 13:00:00 ┆ 2015-03-04 13:00:00 │
│ 26540 ┆ 26579 ┆ 26480 ┆ 26525 ┆ 2341   ┆ 2015-03-04 17:00:00 ┆ 2015-03-04 17:00:00 │
│ 26524 ┆ 26568 ┆ 26502 ┆ 26535 ┆ 1844   ┆ 2015-03-04 21:00:00 ┆ 2015-03-04 21:00:00 │
│ 26565 ┆ 26579 ┆ 26475 ┆ 26480 ┆ 1725   ┆ 2015-03-05 09:00:00 ┆ 2015-03-05 09:00:00 │
│ 26484 ┆ 26499 ┆ 26435 ┆ 26453 ┆ 1641   ┆ 2015-03-05 13:00:00 ┆ 2015-03-05 13:00:00 │
│ 26453 ┆ 26586 ┆ 26450 ┆ 26574 ┆ 1624   ┆ 2015-03-05 17:00:00 ┆ 2015-03-05 17:00:00 │
│ 26576 ┆ 26627 ┆ 26462 ┆ 26475 ┆ 1835   ┆ 2015-03-05 21:00:00 ┆ 2015-03-05 21:00:00 │
│ 26460 ┆ 26484 ┆ 26170 ┆ 26200 ┆ 3683   ┆ 2015-03-06 17:00:00 ┆ 2015-03-06 17:00:00 │
│ 26200 ┆ 26235 ┆ 25982 ┆ 25987 ┆ 2482   ┆ 2015-03-06 21:00:00 ┆ 2015-03-06 21:00:00 │
│ 26073 ┆ 26096 ┆ 26036 ┆ 26063 ┆ 1803   ┆ 2015-03-09 09:00:00 ┆ 2015-03-09 09:00:00 │
│ 26062 ┆ 26125 ┆ 26056 ┆ 26076 ┆ 2194   ┆ 2015-03-09 13:00:00 ┆ 2015-03-09 13:00:00 │
│ 26075 ┆ 26129 ┆ 26006 ┆ 26027 ┆ 2243   ┆ 2015-03-09 17:00:00 ┆ 2015-03-09 17:00:00 │
│ 26027 ┆ 26045 ┆ 26001 ┆ 26022 ┆ 1418   ┆ 2015-03-09 21:00:00 ┆ 2015-03-09 21:00:00 │
│ 25962 ┆ 25962 ┆ 25825 ┆ 25861 ┆ 3078   ┆ 2015-03-10 09:00:00 ┆ 2015-03-10 09:00:00 │
│ 25860 ┆ 25950 ┆ 25780 ┆ 25943 ┆ 3328   ┆ 2015-03-10 13:00:00 ┆ 2015-03-10 13:00:00 │
│ 25944 ┆ 26079 ┆ 25894 ┆ 25937 ┆ 3691   ┆ 2015-03-10 17:00:00 ┆ 2015-03-10 17:00:00 │
│ 25935 ┆ 25975 ┆ 25873 ┆ 25916 ┆ 1862   ┆ 2015-03-10 21:00:00 ┆ 2015-03-10 21:00:00 │
│ 25950 ┆ 25950 ┆ 25885 ┆ 25925 ┆ 1925   ┆ 2015-03-11 09:00:00 ┆ 2015-03-11 09:00:00 │
│ 25921 ┆ 25934 ┆ 25821 ┆ 25882 ┆ 2765   ┆ 2015-03-11 13:00:00 ┆ 2015-03-11 13:00:00 │
│ 25878 ┆ 25883 ┆ 25653 ┆ 25704 ┆ 3878   ┆ 2015-03-11 17:00:00 ┆ 2015-03-11 17:00:00 │
│ 25708 ┆ 25750 ┆ 25660 ┆ 25685 ┆ 1977   ┆ 2015-03-11 21:00:00 ┆ 2015-03-11 21:00:00 │
│ 25660 ┆ 25860 ┆ 25626 ┆ 25809 ┆ 3670   ┆ 2015-03-12 09:00:00 ┆ 2015-03-12 09:00:00 │
│ 25810 ┆ 25812 ┆ 25732 ┆ 25745 ┆ 2830   ┆ 2015-03-12 13:00:00 ┆ 2015-03-12 13:00:00 │
│ 25746 ┆ 25759 ┆ 25615 ┆ 25643 ┆ 3401   ┆ 2015-03-12 17:00:00 ┆ 2015-03-12 17:00:00 │
│ 25646 ┆ 25669 ┆ 25562 ┆ 25648 ┆ 2001   ┆ 2015-03-12 21:00:00 ┆ 2015-03-12 21:00:00 │
│ 25720 ┆ 25846 ┆ 25720 ┆ 25787 ┆ 2507   ┆ 2015-03-13 09:00:00 ┆ 2015-03-13 09:00:00 │
│ 25788 ┆ 25872 ┆ 25761 ┆ 25841 ┆ 2834   ┆ 2015-03-13 13:00:00 ┆ 2015-03-13 13:00:00 │
│ 25840 ┆ 25918 ┆ 25785 ┆ 25798 ┆ 3179   ┆ 2015-03-13 17:00:00 ┆ 2015-03-13 17:00:00 │
│ 25810 ┆ 25915 ┆ 25800 ┆ 25912 ┆ 1935   ┆ 2015-03-13 21:00:00 ┆ 2015-03-13 21:00:00 │
│ 25875 ┆ 25941 ┆ 25860 ┆ 25908 ┆ 1692   ┆ 2015-03-16 09:00:00 ┆ 2015-03-16 09:00:00 │
│ 25909 ┆ 25910 ┆ 25780 ┆ 25790 ┆ 1932   ┆ 2015-03-16 13:00:00 ┆ 2015-03-16 13:00:00 │
│ 25791 ┆ 25850 ┆ 25706 ┆ 25739 ┆ 2503   ┆ 2015-03-16 17:00:00 ┆ 20

In [10]:
def resample(
    data: pl.DataFrame, timeframe, offset: dt.timedelta | None = None
) -> pl.DataFrame:
    return (
        data.set_sorted("datetime")
        .group_by_dynamic(
            index_column="datetime",
            every=timeframe,
            period=timeframe,
            truncate=True,
            offset=offset,
        )
        .agg(
            [
                pl.col("open").first().alias("open"),
                pl.col("high").max().alias("high"),
                pl.col("low").min().alias("low"),
                pl.col("close").last().alias("close"),
                pl.col("volume").sum().alias("volume"),
            ]
        )
    )

ohlc_resampled = resample(bnf, '60m', pd.Timedelta(minutes=15))

# bnf_df = bnf.to_pandas()
# bnf_df.set_index(bnf_df['datetime'], inplace=True)
# ohlc_15min = bnf_df.resample('60min').agg({
#     'open': 'first',
#     'high': 'max',
#     'low': 'min',
#     'close': 'last',
# })

# ohlc_15min.dropna(inplace=True)

# ohlc_15min.reset_index(inplace=True)

# bnf_1hr = ohlc_15min
bnf_1hr = ohlc_resampled
bnf_final = bnf_1hr.to_pandas()
bnf_final['datetime'] = pd.to_datetime(bnf_final['datetime'])
# bnf_final
# bnf_1hr

/tmp/ipykernel_2612/3394447139.py:13: DeprecationWarning: `truncate` is deprecated and will be removed in a future version. Please replace `truncate=True` with `label='left'` to silence this warning.
  .agg(


In [11]:
bnf_final

datetime      open      high       low     close  volume
0    2022-01-21 09:15:00   7705.65   7708.70   7645.80   7685.10     0.0
1    2022-01-21 10:15:00   7684.95   7690.55   7616.75   7641.30     0.0
2    2022-01-21 11:15:00   7641.05   7647.55   7616.65   7646.95     0.0
3    2022-01-21 12:15:00   7647.00   7676.75   7639.70   7675.40     0.0
4    2022-01-21 13:15:00   7675.10   7675.10   7607.25   7607.95     0.0
5    2022-01-21 14:15:00   7608.05   7608.45   7490.45   7555.25     0.0
6    2022-01-21 15:15:00   7556.05   7567.35   7543.80   7563.60     0.0
7    2022-01-24 09:15:00   7548.90   7559.00   7392.75   7404.40     0.0
8    2022-01-24 10:15:00   7403.35   7403.35   7346.25   7357.25     0.0
9    2022-01-24 11:15:00   7357.20   7365.05   7301.05   7312.80     0.0
10   2022-01-24 12:15:00   7313.20   7316.80   7269.50   7309.30     0.0
11   2022-01-24 13:15:00   7309.10   7310.55   7188.65   7191.30     0.0
12   2022-01-24 14:15:00   7191.60   7282.10   7191.60   7278.80     0.0
13   2022-01-24 15:15:00   7279.20   7279.90   7243.90   7251.75     0.0
14   2022-01-25 09:15:00   7191.40   7340.80   7098.30   7293.35     0.0
15   2022-01-25 10:15:00   7293.70   7308.00   7254.75   7303.65     0.0
16   2022-01-25 11:15:00   7303.80   7320.55   7296.65   7306.90     0.0
17   2022-01-25 12:15:00   7307.20   7313.75   7276.95   7308.10     0.0
18   2022-01-25 13:15:00   7308.40   7348.70   7301.50   7340.60     0.0
19   2022-01-25 14:15:00   7340.20   7365.25   7325.90   7364.20     0.0
20   2022-01-25 15:15:00   7365.15   7374.60   7346.70   7348.55     0.0
21   2022-01-27 09:15:00   7307.30   7313.30   7198.20   7228.10     0.0
22   2022-01-27 10:15:00   7227.30   7249.75   7207.10   7241.85     0.0
23   2022-01-27 11:15:00   7241.75   7246.20   7194.35   7195.15     0.0
24   2022-01-27 12:15:00   7195.20   7261.65   7186.45   7260.20     0.0
25   2022-01-27 13:15:00   7260.95   7308.55   7254.10   7297.95     0.0
26   2022-01-27 14:15:00   7298.10   7360.20   7298.10   7353.55     0.0
27   2022-01-27 15:15:00   7353.95   7364.45   7341.20   7358.95     0.0
28   2022-01-28 09:15:00   7420.50   7519.70   7415.45   7504.75     0.0
29   2022-01-28 10:15:00   7504.80   7555.45   7490.65   7549.45     0.0
30   2022-01-28 11:15:00   7549.65   7579.50   7548.70   7573.30     0.0
31   2022-01-28 12:15:00   7573.55   7577.35   7544.70   7547.10     0.0
32   2022-01-28 13:15:00   7547.35   7560.50   7463.95   7465.10     0.0
33   2022-01-28 14:15:00   7464.75   7490.25   7392.45   7411.05     0.0
34   2022-01-28 15:15:00   7412.20   7423.85   7401.45   7414.40     0.0
35   2022-01-31 09:15:00   7504.05   7529.95   7466.65   7480.65     0.0
36   2022-01-31 10:15:00   7481.10   7510.40   7459.15   7508.95     0.0
37   2022-01-31 11:15:00   7509.15   7524.50   7496.55   7518.95     0.0
38   2022-01-31 12:15:00   7519.40   7541.60   7497.10   7538.75     0.0
39   2022-01-31 13:15:00   7538.10   7543.70   7514.15   7525.00     0.0
40   2022-01-31 14:15:00   7525.40   7540.35   7511.35   7516.45     0.0
41   2022-01-31 15:15:00   7516.10   7519.80   7506.55   7513.50     0.0
42   2022-02-01 09:15:00   7586.70   7586.70   7528.15   7569.90     0.0
43   2022-02-01 10:15:00   7569.90   7589.55   7560.35   7579.45     0.0
44   2022-02-01 11:15:00   7579.60   7585.30   7509.95   7566.65     0.0
45   2022-02-01 12:15:00   7566.70   7586.20   7472.20   7475.80     0.0
46   2022-02-01 13:15:00   7476.30   7574.50   7462.55   7567.45     0.0
47   2022-02-01 14:15:00   7567.70   7610.05   7566.40   7593.10     0.0
48   2022-02-01 15:15:00   7593.00   7610.55   7592.20   7605.90     0.0
49   2022-02-02 09:15:00   7640.70   7715.40   7635.90   7706.50     0.0
50   2022-02-02 10:15:00   7706.50   7713.40   7671.70   7695.10     0.0
51   2022-02-02 11:15:00   7695.35   7707.00   7689.10   7690.85     0.0
52   2022-02-02 12:15:00   7689.90   7692.40   7675.70   7686.10     0.0
53   2022-02-02 13:15:00   7686.60   7696.10   7662.15   7686.10     0.0
5

In [1512]:
# # bnf_final = bnf_1hr
# bnf_final['datetime'] = pd.to_datetime(bnf_final['datetime'])
# bnf_final

In [456]:
def generate_signals2(df):
    df['close'] = pd.to_numeric(df['close'], errors='coerce')
    df['MA20'] = df['close'].rolling(window=48).mean()
    df['MA10'] = df['close'].rolling(window=10).mean()

    df['Buy_Signal'] = 0
    df['Sell_Signal'] = 0
    
    # Generate signals using boolean masking
    buy_signal_mask = (
        (df['MA20'] > df['MA20'].shift(1))
        & (df['MA20'].shift(1) > df['MA20'].shift(2))
        & (df['MA20'].shift(2) > df['MA20'].shift(3)) 
        # & (df['MA20'].shift(3) > df['MA20'].shift(4)) 
        # & (df['MA20'].shift(4) > df['MA20'].shift(5)) 
        # & (df['MA20'].shift(5) > df['MA20'].shift(6))
        # & (df['MA20'].shift(6) > df['MA20'].shift(7)) 
        # & (df['MA20'].shift(7) > df['MA20'].shift(8))
        # & (df['MA20'].shift(8) > df['MA20'].shift(9))
    )

    sell_signal_mask = (
        (df['MA20'] < df['MA20'].shift(1))
        & (df['MA20'].shift(1) < df['MA20'].shift(2))
        & (df['MA20'].shift(2) < df['MA20'].shift(3))
        # & (df['MA20'].shift(3) < df['MA20'].shift(4))
        # & (df['MA20'].shift(4) < df['MA20'].shift(5))
        # & (df['MA20'].shift(5) < df['MA20'].shift(6))
        # & (df['MA20'].shift(6) < df['MA20'].shift(7))
        # & (df['MA20'].shift(7) < df['MA20'].shift(8))
        # & (df['MA20'].shift(8) < df['MA20'].shift(9))
    )
    
    df.loc[buy_signal_mask, 'Buy_Signal'] = 1
    df.loc[sell_signal_mask, 'Sell_Signal'] = 1
    
    return df

In [457]:
# bnf

In [458]:
# signals_df2 = generate_signals2(bnf_final)
# bnf = bnf.to_pandas()
signals_df2 = generate_signals2(bnf)
# signals_df2

In [459]:
signals_df2 = signals_df2.rename(columns={'open': 'o', 'high': 'h', 'low': 'l', 'close': 'c'})

In [460]:
# signals_df2['datetime'] = signals_df2.index

In [461]:
# signals_df2

In [462]:
# signals_df3 = signals_df2.loc[signals_df2['Buy_Signal'] == 1]
# signals_df3

In [463]:
#Positional

def execute(df):
    
    trade_book = []
    in_trade = False
    signal_entry_price = 100000
    signal_initial_sl = 0
    already_signal_exists = False
    is_trailing_active = False
    portfolio_value = 1000000

    for i in range(1, len(df)):
        points = 0
        current_candle_open = df.iloc[i]['o']
        current_candle_high = df.iloc[i]['h']
        current_candle_low = df.iloc[i]['l']
        current_candle_close = df.iloc[i]['c']
        current_moving_average_price = df.iloc[i]['MA10']
    
        if not in_trade:
            if df.iloc[i]['Buy_Signal'] == 1:
                if not already_signal_exists:
                    # Fresh Buy Signal
                    signal_entry_price = current_candle_high
                    signal_initial_sl = current_candle_low
                    signal_creation_time = df.iloc[i]['datetime']
                    already_signal_exists = True

                    if (signal_entry_price - signal_initial_sl > 400):
                        # Skip Signal Candle Due To Big Size
                        already_signal_exists = False
                        signal_entry_price = 100000
                        signal_initial_sl = 0
                    
                else:
                    if current_candle_open > signal_entry_price:
                        # Gap Up Open, SKIP trade
                        already_signal_exists = False
                        signal_entry_price = 100000
                        signal_initial_sl = 0
                    elif current_candle_high < signal_entry_price:
                        # Better Candle
                        signal_entry_price = current_candle_high
                        signal_initial_sl = current_candle_low
                        signal_creation_time = df.iloc[i]['datetime']

                        if (signal_entry_price - signal_initial_sl > 400):
                            # Skip Signal Candle Due To Big Size
                            already_signal_exists = False
                            signal_entry_price = 100000
                            signal_initial_sl = 0
                    
                    elif current_candle_high > signal_entry_price:
                        # Entry Triggered
                        in_trade = True
                        entry_time = df.iloc[i]['datetime']
                        entry_price = signal_entry_price
                        points = 0
            else:
                # Discard Existing Signal
                already_signal_exists = False
                signal_entry_price = 100000
                signal_initial_sl = 0
    
        else:
            trade_entry_price = signal_entry_price
            trade_initial_sl = signal_initial_sl
            trade_final_sl = signal_initial_sl
    
            if not is_trailing_active and current_candle_low > current_moving_average_price:
                is_trailing_active = True
    
            if not is_trailing_active:
                if current_candle_low < trade_initial_sl:
                    # Initial SL Hit
                    in_trade = False
                    points = trade_initial_sl - trade_entry_price
                    exit_price = trade_initial_sl
                    exit_time = df.iloc[i]['datetime']
    
            else:
                trade_final_sl = max(trade_initial_sl, current_moving_average_price)
                
                if current_candle_low < trade_initial_sl:
                    if trade_initial_sl >= current_moving_average_price:
                        # Despite Trailing, Initial SL hit
                        in_trade = False
                        points = trade_initial_sl - trade_entry_price
                        exit_price = trade_initial_sl
                        exit_time = df.iloc[i]['datetime']
                    
                elif current_candle_close < trade_final_sl:
                    # Price Closed below TSL i.e. MA10 , TSL Hit
                    in_trade = False
                    points = current_candle_close - trade_entry_price
                    exit_price = current_candle_close
                    exit_time = df.iloc[i]['datetime']
                    is_trailing_active = False

    
            if points:
                qty = 1000000 * 5 / entry_price
                slippage = 0.0005 * (entry_price + exit_price)
                # slippage = 10
                final_points = points - slippage
                # final_points = points
                trade = {
                    'Signal Generated At': signal_creation_time,
                    'Entry Time': entry_time,
                    'Entry Price': entry_price,
                    'Initial SL': trade_initial_sl,
                    'Final SL': trade_final_sl,
                    'Exit Time': exit_time,
                    'Exit Price': exit_price,
                    'Points Captured': points,
                    'After Costs': final_points,
                    'Qty': qty,
                    'ROI%': (final_points * qty / portfolio_value) * 100,
                    'Trade Year': entry_time.year,
                    'Trade Month': entry_time.month
                }
                trade_book.append(trade)
                points = 0
                in_trade = False
                already_signal_exists = False
                is_trailing_active = False

    trade_book_df = pd.DataFrame(trade_book)
    return trade_book_df
        

In [471]:
new_tb = execute(signals_df2)
new_tb

Signal Generated At          Entry Time  Entry Price  Initial SL  \
0   2015-03-25 09:00:00 2015-03-25 13:00:00        26280       26212   
1   2015-03-31 13:00:00 2015-03-31 17:00:00        26421       26274   
2   2015-04-01 13:00:00 2015-04-01 17:00:00        26338       26238   
3   2015-04-09 13:00:00 2015-04-09 17:00:00        26598       26492   
4   2015-04-16 21:00:00 2015-04-17 09:00:00        26659       26601   
5   2015-04-21 13:00:00 2015-04-21 17:00:00        26865       26753   
6   2015-04-28 13:00:00 2015-04-28 17:00:00        27057       26970   
7   2015-05-05 09:00:00 2015-05-05 13:00:00        26844       26779   
8   2015-05-08 09:00:00 2015-05-08 13:00:00        26930       26855   
9   2015-05-12 09:00:00 2015-05-12 13:00:00        26954       26860   
10  2015-05-15 17:00:00 2015-05-15 21:00:00        27449       27284   
11  2015-05-20 09:00:00 2015-05-20 13:00:00        27293       27186   
12  2015-05-22 21:00:00 2015-05-25 09:00:00        27127       27072   
13  2015-06-15 13:00:00 2015-06-15 17:00:00        26932       26738   
14  2015-06-17 13:00:00 2015-06-17 17:00:00        26892       26862   
15  2015-08-07 21:00:00 2015-08-10 09:00:00        24932       24875   
16  2015-08-17 13:00:00 2015-08-17 17:00:00        25960       25928   
17  2015-08-25 21:00:00 2015-08-26 09:00:00        26777       26662   
18  2015-08-27 13:00:00 2015-08-27 17:00:00        26417       26303   
19  2015-08-28 13:00:00 2015-08-28 17:00:00        26566       26410   
20  2015-09-03 21:00:00 2015-09-04 09:00:00        26430       26339   
21  2015-09-29 13:00:00 2015-09-29 17:00:00        26535       26441   
22  2015-10-06 13:00:00 2015-10-06 17:00:00        26530       26439   
23  2015-10-09 13:00:00 2015-10-09 17:00:00        26670       26454   
24  2015-10-16 13:00:00 2015-10-16 17:00:00        27187       27070   
25  2015-10-19 13:00:00 2015-10-19 17:00:00        26979       26929   
26  2015-10-20 13:00:00 2015-10-20 17:00:00        27140       27004   
27  2015-10-26 13:00:00 2015-10-26 17:00:00        26888       26770   
28  2015-12-04 13:00:00 2015-12-04 17:00:00        25267       25157   
29  2015-12-08 13:00:00 2015-12-08 17:00:00        25490       25437   
30  2015-12-11 09:00:00 2015-12-11 13:00:00        25418       25293   
31  2015-12-15 09:00:00 2015-12-15 13:00:00        25375       25312   
32  2015-12-16 13:00:00 2015-12-16 17:00:00        25315       25220   
33  2015-12-21 09:00:00 2015-12-21 13:00:00        25212       25145   
34  2015-12-22 09:00:00 2015-12-22 13:00:00        25360       25308   
35  2016-01-05 09:00:00 2016-01-05 13:00:00        25446       25318   
36  2016-01-12 09:00:00 2016-01-12 13:00:00        25939       25846   
37  2016-01-13 13:00:00 2016-01-13 17:00:00        25585       25516   
38  2016-01-15 09:00:00 2016-01-15 13:00:00        25825       25658   
39  2016-01-19 17:00:00 2016-01-19 21:00:00        26027       25860   
40  2016-01-22 13:00:00 2016-01-22 17:00:00        26199       26120   
41  2016-01-29 13:00:00 2016-01-29 17:00:00        26591       26502   
42  2016-02-10 17:00:00 2016-02-10 21:00:00        28280       28075   
43  2016-02-16 09:00:00 2016-02-16 13:00:00        28681       28425   
44  2016-02-22 21:00:00 2016-02-23 09:00:00        29020       28910   
45  2016-02-26 21:00:00 2016-02-29 09:00:00        29476       29152   
46  2016-03-03 09:00:00 2016-03-03 13:00:00        29325       29248   
47  2016-03-08 09:00:00 2016-03-08 13:00:00        30010       29650   
48  2016-03-09 17:00:00 2016-03-09 21:00:00        29588       29301   
49  2016-04-11 21:00:00 2016-04-12 09:00:00        29388       29310   
50  2016-04-13 13:00:00 2016-04-13 17:00:00        29224       29058   
51  2016-04-14 21:00:00 2016-04-15 17:00:00        28899       28715   
52  2016-04-22 09:00:00 2016-04-22 13:00:00        29401       29267   
53  2016-04-25 13:00:00 2016-04-25 17:00:00        29190       29072   
54  2016-04-27 13:00:00 2016-04-27 17:00:00 

In [465]:
# new_tb.to_csv('Reliance_14_12_6_30min_5xLev_MTrend_TB.csv')

In [466]:
new_tb['Points Captured'].sum()
tradebook_buy_side = new_tb

In [467]:
stats_df5 = pd.DataFrame(index=range(2015, 2024), columns=['Total ROI', 'Total Trades', 'Win Rate', 'Avg Profit% per Trade', 'Avg Loss% per Trade', 'Max Drawdown', 'ROI/DD Ratio'])

# Iterate over each year
for year in range(2015, 2024):
    # Filter trades for the current year
    year_trades = new_tb[(new_tb['Trade Year'] == year)]
    
    # Calculate total ROI
    total_roi = year_trades['ROI%'].sum()
    
    # Calculate total number of trades
    total_trades = len(year_trades)
    
    # Calculate win rate
    win_rate = (year_trades['ROI%'] > 0).mean()*100
    
    # Calculate average profit per trade
    avg_profit = year_trades[year_trades['ROI%'] > 0]['ROI%'].mean()
    
    # Calculate average loss per trade
    avg_loss = year_trades[year_trades['ROI%'] < 0]['ROI%'].mean()
    
    # Calculate maximum drawdown
    max_drawdown = (year_trades['ROI%'].cumsum() - year_trades['ROI%'].cumsum().cummax()).min()
    
    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)
    # 
    # Store the statistics in the DataFrame
    stats_df5.loc[year] = [total_roi, total_trades, win_rate, avg_profit, avg_loss, max_drawdown, roi_dd_ratio]

# Calculate overall statistics
overall_total_roi = stats_df5['Total ROI'].sum()
overall_total_trades = stats_df5['Total Trades'].sum()
overall_win_rate = (new_tb['ROI%'] > 0).mean() * 100
overall_avg_profit = new_tb[new_tb['ROI%'] > 0]['ROI%'].mean()
overall_avg_loss = new_tb[new_tb['ROI%'] < 0]['ROI%'].mean()
overall_max_drawdown = (new_tb['ROI%'].cumsum() - new_tb['ROI%'].cumsum().cummax()).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df5.loc['Overall'] = [overall_total_roi, overall_total_trades, overall_win_rate, overall_avg_profit, overall_avg_loss, overall_max_drawdown, overall_roi_dd_ratio]
stats_df5

# import pandas as pd

# # Assuming 'new_tb' and 'stats_df5' are defined elsewhere

# # Create a list to store monthly statistics data
# monthly_data = []

# # Iterate over each year
# for year in range(2022, 2024):
#     for month in range(1, 13):
#         # Filter trades for the current year and month
#         month_trades = new_tb[(new_tb['Trade Year'] == year) & (new_tb['Trade Month'] == month)]
        
#         # Calculate total ROI
#         total_roi = month_trades['ROI%'].sum()
        
#         # Calculate total number of trades
#         total_trades = len(month_trades)
        
#         # Calculate win rate
#         win_rate = (month_trades['ROI%'] > 0).mean() * 100
        
#         # Calculate average profit per trade
#         avg_profit = month_trades[month_trades['ROI%'] > 0]['ROI%'].mean()
        
#         # Calculate average loss per trade
#         avg_loss = month_trades[month_trades['ROI%'] < 0]['ROI%'].mean()
        
#         # Calculate maximum drawdown
#         max_drawdown = (month_trades['ROI%'].cumsum() - month_trades['ROI%'].cumsum().cummax()).min()
        
#         # Calculate ROI/DD ratio
#         roi_dd_ratio = total_roi / abs(max_drawdown)
        
#         # Append the statistics data to the list
#         monthly_data.append({'Year': year,
#                              'Month': month,
#                              'Total ROI': total_roi,
#                              'Total Trades': total_trades,
#                              'Win Rate': win_rate,
#                              'Avg Profit% per Trade': avg_profit,
#                              'Avg Loss% per Trade': avg_loss,
#                              'Max Drawdown': max_drawdown,
#                              'ROI/DD Ratio': roi_dd_ratio})

# # Create a DataFrame from the list of monthly statistics data
# monthly_stats_df = pd.DataFrame(monthly_data)

# # Set index for the DataFrame
# monthly_stats_df.set_index(['Year', 'Month'], inplace=True)

# # Display the DataFrame
# monthly_stats_df

Total ROI Total Trades   Win Rate Avg Profit% per Trade  \
2015      33.021732           35  31.428571              6.796608   
2016      76.910755           48  39.583333              7.709783   
2017       -6.08989           55  29.090909              3.395287   
2018      27.520228           46  43.478261              3.715187   
2019      70.668528           59  33.898305              7.161699   
2020       84.82639           59  28.813559             10.809328   
2021       6.468526           40       32.5                4.0715   
2022      14.640724           55  23.636364              7.885091   
2023      16.467452           48  27.083333              5.915911   
Overall  324.434446        445.0  31.777778               6.51964   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio  
2015              -1.739207   -13.409132      2.46263  
2016              -2.399142   -18.777759     4.095843  
2017              -1.549089   -25.126487    -0.242369  
2018              -1.799366   -13.620262     2.020536  
2019              -1.860653   -18.227919     3.876939  
2020              -2.355528   -21.383137     3.966976  
2021              -1.720777   -17.084616     0.378617  
2022              -2.092035   -33.286466      0.43984  
2023               -1.72684   -27.423572     0.600485  
Overall           -1.921897   -33.286466     9.746738

In [468]:
# Crude -> 14, 14, 5 -> Long

In [469]:
# 14, 12, 6 -> Reliance 30 mins TF -> Best , 5x Leverage

In [747]:
# 8, 25, 3 : MIDCP -> Buy Best Variation

In [1203]:
# 48, 12, 3 : BNF -> Long Best Variation

In [470]:
new_tb.to_csv('Gold 48_10_3 MTrend Long.csv')

In [ ]:
# signals_df2

In [ ]:
# Final Attempt !
# With Option Buying

async def execute_opt_tb(df):
    
    trade_book = []
    in_trade = False
    signal_entry_price = 100000
    signal_initial_sl = 0
    already_signal_exists = False
    is_trailing_active = False
    strike = 0
    ce_data = pd.DataFrame()

    for i in range(1, len(df)):
        # print(df.iloc[i])
        points = 0
        current_candle_open = df.iloc[i]['o']
        current_candle_high = df.iloc[i]['h']
        current_candle_low = df.iloc[i]['l']
        current_candle_close = df.iloc[i]['c']
        current_moving_average_price = df.iloc[i]['MA10']
        # print(current_moving_average_price)
        
    
        if not in_trade:
            if df.iloc[i]['Buy_Signal'] == 1:
                if not already_signal_exists:
                    # Fresh Buy Signal
                    signal_entry_price = current_candle_high
                    signal_initial_sl = current_candle_low
                    signal_creation_time = df.iloc[i]['datetime']
                    already_signal_exists = True
                    
                else:
                    if current_candle_open > signal_entry_price:
                        # Gap Found, Skip Trade
                        already_signal_exists = False
                        signal_entry_price = 100000
                        signal_initial_sl = 0
                    elif current_candle_high < signal_entry_price:
                        # Better Candle
                        signal_entry_price = current_candle_high
                        signal_initial_sl = current_candle_low
                        signal_creation_time = df.iloc[i]['datetime']
                    
                    elif current_candle_high > signal_entry_price:
                        # Entry Triggered
                        in_trade = True
                        entry_time = df.iloc[i]['datetime']
                        strike = int(signal_entry_price / 100) * 100
                        points = 0
            else:
                # Discard Existing Signal
                already_signal_exists = False
                signal_entry_price = 100000
                signal_initial_sl = 0
    
        else:
            trade_entry_price = signal_entry_price
            trade_initial_sl = signal_initial_sl
            trade_final_sl = signal_initial_sl
            entry_date = entry_time.date()
            
            # Add timedelta to the date
            expiry_date = entry_date + dt.timedelta(days=7)
            final_expiry_date = get_expiry(expiry_date)

            # print(entry_time.date)
            # print(type(entry_time.date))
            option_contract = get_option_contract_name('bnf', strike, final_expiry_date, AssetClass.CALL)
            option_df = await fetch_option_data(
                index='bnf',
                expiry=final_expiry_date,
                strike=strike,
                asset_class=AssetClass.CALL,
                start_date=entry_date,
                start_time=dt.time(9, 15),
                end_date=entry_date,
                end_time=dt.time(15, 30),
            )
            if len(option_df) == 63:
                in_trade=False
                points = 0
                already_signal_exists = False
                continue
            assert len(option_df) != 63
            ce_data = option_df.to_pandas()
            ce_data.set_index('datetime', inplace=True)
            idx = pd.date_range(start=ce_data.index.min(), end=ce_data.index.max(), freq='1min')  # '1T' represents 1 minute frequency
            ce_data = ce_data.reindex(idx)
            ce_data = ce_data.ffill()
            # print(ce_data)
            
            option_entry_price = ce_data.at[entry_time.time(), 'c']
    
            if not is_trailing_active and current_candle_low > current_moving_average_price:
                is_trailing_active = True
    
            if not is_trailing_active:
                if current_candle_low < trade_initial_sl:
                    # Initial SL Hit
                    exit_time = df.iloc[i]['datetime']
                    exit_date = exit_time.date()
                    in_trade = False
                    # points = trade_initial_sl - trade_entry_price
                    option_df = await fetch_option_data(
                        index='bnf',
                        expiry=final_expiry_date,
                        strike=strike,
                        asset_class=AssetClass.CALL,
                        start_date=exit_date,
                        start_time=dt.time(9, 15),
                        end_date=exit_date,
                        end_time=exit_time.time(),
                    )
                    if len(option_df) == 63:
                        in_trade=False
                        points = 0
                        already_signal_exists = False
                        is_trailing_active = False
                        continue
                    assert len(option_df) != 63
                    # print('Initial SL /n', option_df)
                    # print(type(option_df))
                    option_exit_price = option_df['c'][-1]
                    points = option_exit_price - option_entry_price
                    exit_price = option_exit_price
                    exit_price_on_spot = trade_initial_sl
    
            else:
                trade_final_sl = max(trade_initial_sl, current_moving_average_price)
                if current_candle_close < trade_final_sl:
                    # Price Closed below TSL i.e. MA10 , TSL Hit
                    exit_time = df.iloc[i]['datetime']
                    in_trade = False
                    option_df = await fetch_option_data(
                        index='bnf',
                        expiry=final_expiry_date,
                        strike=strike,
                        asset_class=AssetClass.CALL,
                        start_date=entry_time.date(),
                        start_time=dt.time(9, 15),
                        end_date=exit_time.date(),
                        end_time=exit_time.time(),
                    )
                    if len(option_df) == 63:
                        in_trade=False
                        points = 0
                        is_trailing_active = False
                        already_signal_exists = False
                        continue
                    assert len(option_df) != 63
                    # print('TSL /n', option_df)
                    # print(type(option_df))
                    option_exit_price = option_df['c'][-1]
                    points = option_exit_price - option_entry_price
                    exit_price = option_exit_price
                    exit_price_on_spot = current_candle_close
    
            if points:
                qty = int((1000000 / (option_entry_price[0])) / 15) * 15
                qty_in_lots = (qty / 15) / 10 # We will use 10% capital for Option Buying, Hence -> qty_in_lots / 10
                points_after_costs = ((points[0] * 0.95) if points[0] > 0 else (points[0] * 1.05))
                trade = {
                    'Signal Generated At': signal_creation_time,
                    'Contract Name': option_contract,
                    'Entry Time': entry_time,
                    'Entry Price On Spot': trade_entry_price,
                    'Entry Price On Option': option_entry_price[0],
                    'Initial SL On Spot': trade_initial_sl,
                    'Final SL On Spot': trade_final_sl,
                    'Exit Time': exit_time,
                    'Exit Price On Spot': exit_price_on_spot,
                    'Exit Price On Option': option_exit_price,
                    'Points Captured On Options': points[0],
                    'After Costs': points_after_costs,
                    'Quantity In Lots': qty_in_lots,
                    'ROI%': (points_after_costs) * qty_in_lots * 15 / 10000,
                    'Trade Year': entry_time.year,
                }
                # print(trade)
                trade_book.append(trade)
                points = 0
                points_after_costs = 0
                in_trade = False
                is_trailing_active = False
                already_signal_exists = False
                qty = 0
                qty_in_lots = 0
                strike = 0

    trade_book_df = pd.DataFrame(trade_book)
    return trade_book_df
        

In [ ]:
new_tb_intra = await execute_opt_tb(signals_df2)

In [ ]:
new_tb_intra

In [ ]:
options_pnl = new_tb_intra['After Costs'].sum()
options_pnl

In [ ]:
stats_df6 = pd.DataFrame(index=range(2017, 2024), columns=['Total ROI', 'Total Trades', 'Win Rate', 'Avg Profit% per Trade', 'Avg Loss% per Trade', 'Max Drawdown', 'ROI/DD Ratio'])

# Iterate over each year
for year in range(2017, 2024):
    # Filter trades for the current year
    year_trades = new_tb_intra[(new_tb_intra['Trade Year'] == year)]
    
    # Calculate total ROI
    total_roi = year_trades['ROI%'].sum()
    
    # Calculate total number of trades
    total_trades = len(year_trades)
    
    # Calculate win rate
    win_rate = (year_trades['ROI%'] > 0).mean()*100
    
    # Calculate average profit per trade
    avg_profit = year_trades[year_trades['ROI%'] > 0]['ROI%'].mean()
    
    # Calculate average loss per trade
    avg_loss = year_trades[year_trades['ROI%'] < 0]['ROI%'].mean()
    
    # Calculate maximum drawdown
    max_drawdown = (year_trades['ROI%'].cumsum() - year_trades['ROI%'].cumsum().cummax()).min()
    
    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)
    
    # Store the statistics in the DataFrame
    stats_df6.loc[year] = [total_roi, total_trades, win_rate, avg_profit, avg_loss, max_drawdown, roi_dd_ratio]

# Calculate overall statistics
overall_total_roi = stats_df6['Total ROI'].sum()
overall_total_trades = stats_df6['Total Trades'].sum()
overall_win_rate = (new_tb_intra['ROI%'] > 0).mean() * 100
overall_avg_profit = new_tb_intra[new_tb_intra['ROI%'] > 0]['ROI%'].mean()
overall_avg_loss = new_tb_intra[new_tb_intra['ROI%'] < 0]['ROI%'].mean()
overall_max_drawdown = (new_tb_intra['ROI%'].cumsum() - new_tb_intra['ROI%'].cumsum().cummax()).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df6.loc['Overall'] = [overall_total_roi, overall_total_trades, overall_win_rate, overall_avg_profit, overall_avg_loss, overall_max_drawdown, overall_roi_dd_ratio]
stats_df6

In [ ]:
# Options Tradebook - Long Bias CE Positional

In [ ]:
new_tb_intra.to_csv('Options Tradebook 1hr Pos3.csv')

In [ ]:
# Final Attempt !
# With Option Selling

# dates_to_ignore = [
#     dt.date(2017, 1, 25),
#     dt.date(2017, 1, 30),
#     dt.date(2017, 2, 3),
#     dt.date(2017, 2, 27),
#     dt.date(2017, 5, 26),
#     dt.date(2017, 6, 9),
#     dt.date(2017, 7, 10),
#     dt.date(2017, 7, 28),
#     dt.date(2017, 7, 31),
#     dt.date(2017, 8, 1),
#     dt.date(2017, 8, 2),
#     dt.date(2017, 8, 24),
# ]

async def execute_opt_tb_sell(df):
    
    trade_book = []
    in_trade = False
    signal_entry_price = 100000
    signal_initial_sl = 0
    already_signal_exists = False
    is_trailing_active = False
    strike = 0
    pe_data = pd.DataFrame()

    for i in range(1, len(df)):
        # print(df.iloc[i])
        points = 0
        current_candle_open = df.iloc[i]['o']
        current_candle_high = df.iloc[i]['h']
        current_candle_low = df.iloc[i]['l']
        current_candle_close = df.iloc[i]['c']
        current_moving_average_price = df.iloc[i]['MA10']
        # print(current_moving_average_price)
        
    
        if not in_trade:
            if df.iloc[i]['Buy_Signal'] == 1:
                if not already_signal_exists:
                    # Fresh Buy Signal
                    signal_entry_price = current_candle_high
                    signal_initial_sl = current_candle_low
                    signal_creation_time = df.iloc[i]['datetime']
                    already_signal_exists = True
                    
                else:
                    if current_candle_open > signal_entry_price:
                        # Gap Found, Skip Trade
                        already_signal_exists = False
                        signal_entry_price = 100000
                        signal_initial_sl = 0
                    elif current_candle_high < signal_entry_price:
                        # Better Candle
                        signal_entry_price = current_candle_high
                        signal_initial_sl = current_candle_low
                        signal_creation_time = df.iloc[i]['datetime']
                    
                    elif current_candle_high > signal_entry_price:
                        # Entry Triggered
                        in_trade = True
                        entry_time = df.iloc[i]['datetime']
                        strike = int(signal_entry_price / 100) * 100
                        points = 0
                        if entry_time.date() in dates_to_ignore:
                            print(entry_time.date(), 'Date Skipped')
                            in_trade=False
                            points = 0
                            already_signal_exists = False
                            continue

            else:
                # Discard Existing Signal
                already_signal_exists = False
                signal_entry_price = 100000
                signal_initial_sl = 0
    
        else:
            trade_entry_price = signal_entry_price
            trade_initial_sl = signal_initial_sl
            trade_final_sl = signal_initial_sl
            entry_date = entry_time.date()
            
            # Add timedelta to the date
            expiry_date = entry_date + dt.timedelta(days=7)
            final_expiry_date = get_expiry(expiry_date)

            # print(entry_time.date)
            # print(type(entry_time.date))
            option_contract = get_option_contract_name('bnf', strike, final_expiry_date, AssetClass.PUT)
            option_df = await fetch_option_data(
                index='bnf',
                expiry=final_expiry_date,
                strike=strike,
                asset_class=AssetClass.PUT,
                start_date=entry_date,
                start_time=dt.time(9, 15),
                end_date=entry_date,
                end_time=dt.time(15, 30),
            )
            if len(option_df) == 63:
                in_trade=False
                points = 0
                already_signal_exists = False
                continue
            assert len(option_df) != 63
            pe_data = option_df.to_pandas()
            pe_data.set_index('datetime', inplace=True)
            idx = pd.date_range(start=pe_data.index.min(), end=pe_data.index.max(), freq='1min')  # '1T' represents 1 minute frequency
            pe_data = pe_data.reindex(idx)
            pe_data = pe_data.ffill()
            # print(pe_data)
            
            print(type(entry_time))
            print(entry_time)
            if (entry_time.time() > dt.time(14, 30, 0)):
                print('################################################')
                in_trade=False
                points = 0
                already_signal_exists = False
                continue
            option_entry_price = pe_data.at[entry_time + dt.timedelta(hours=1), 'c']
    
            if not is_trailing_active and current_candle_low > current_moving_average_price:
                is_trailing_active = True
    
            if not is_trailing_active:
                if current_candle_low < trade_initial_sl:
                    # Initial SL Hit
                    exit_time = df.iloc[i]['datetime']
                    exit_date = exit_time.date()
                    in_trade = False
                    # points = trade_initial_sl - trade_entry_price
                    option_df = await fetch_option_data(
                        index='bnf',
                        expiry=final_expiry_date,
                        strike=strike,
                        asset_class=AssetClass.PUT,
                        start_date=exit_date,
                        start_time=exit_time.time(),
                        end_date=exit_date,
                        end_time=exit_time.time(),
                    )
                    if len(option_df) == 63:
                        in_trade=False
                        points = 0
                        already_signal_exists = False
                        is_trailing_active = False
                        continue
                    assert len(option_df) != 63
                    # print('Initial SL /n', option_df)
                    # print(type(option_df))
                    option_exit_price = option_df['c'][-1]
                    points = option_entry_price - option_exit_price
                    exit_price = option_exit_price
                    exit_price_on_spot = trade_initial_sl
    
            else:
                trade_final_sl = max(trade_initial_sl, current_moving_average_price)
                if current_candle_close < trade_final_sl:
                    # Price Closed below TSL i.e. MA10 , TSL Hit
                    exit_time = df.iloc[i]['datetime']
                    in_trade = False
                    option_df = await fetch_option_data(
                        index='bnf',
                        expiry=final_expiry_date,
                        strike=strike,
                        asset_class=AssetClass.PUT,
                        start_date=entry_time.date(),
                        start_time=dt.time(9, 15),
                        end_date=exit_time.date(),
                        end_time=exit_time.time(),
                    )
                    if len(option_df) == 63:
                        in_trade=False
                        points = 0
                        is_trailing_active = False
                        already_signal_exists = False
                        continue
                    assert len(option_df) != 63
                    # print('TSL /n', option_df)
                    # print(type(option_df))
                    option_exit_price = option_df['c'][-1]
                    points = option_entry_price - option_exit_price
                    exit_price = option_exit_price
                    exit_price_on_spot = current_candle_close
    
            if points:
                qty = 10 * 15
                qty_in_lots = 10 
                points_after_costs = ((points * 0.95) if points > 0 else (points * 1.05))
                trade = {
                    'Signal Generated At': signal_creation_time,
                    'Contract Name': option_contract,
                    'Entry Time': entry_time,
                    'Entry Price On Spot': trade_entry_price,
                    'Entry Price On Option': option_entry_price,
                    'Initial SL On Spot': trade_initial_sl,
                    'Final SL On Spot': trade_final_sl,
                    'Exit Time': exit_time,
                    'Exit Price On Spot': exit_price_on_spot,
                    'Exit Price On Option': option_exit_price,
                    'Points Captured On Options': points,
                    'After Costs': points_after_costs,
                    'Quantity In Lots': qty_in_lots,
                    'ROI%': (points_after_costs) * qty / 10000,
                    'Trade Year': entry_time.year,
                }
                print(trade)
                trade_book.append(trade)
                points = 0
                points_after_costs = 0
                in_trade = False
                is_trailing_active = False
                already_signal_exists = False
                qty = 0
                qty_in_lots = 0
                strike = 0

    trade_book_df = pd.DataFrame(trade_book)
    return trade_book_df
        

In [932]:
pe_sell_tb = await execute_opt_tb_sell(signals_df2)
pe_sell_tb

NameError: name 'execute_opt_tb_sell' is not defined

In [933]:
pe_sell_tb.to_csv('PE Selling TB 1hr Pos.csv')

NameError: name 'pe_sell_tb' is not defined

In [934]:
stats_df6 = pd.DataFrame(index=range(2017, 2024), columns=['Total ROI', 'Total Trades', 'Win Rate', 'Avg Profit% per Trade', 'Avg Loss% per Trade', 'Max Drawdown', 'ROI/DD Ratio'])

# Iterate over each year
for year in range(2017, 2024):
    # Filter trades for the current year
    year_trades = pe_sell_tb[(pe_sell_tb['Trade Year'] == year)]
    
    # Calculate total ROI
    total_roi = year_trades['ROI%'].sum()
    
    # Calculate total number of trades
    total_trades = len(year_trades)
    
    # Calculate win rate
    win_rate = (year_trades['ROI%'] > 0).mean()*100
    
    # Calculate average profit per trade
    avg_profit = year_trades[year_trades['ROI%'] > 0]['ROI%'].mean()
    
    # Calculate average loss per trade
    avg_loss = year_trades[year_trades['ROI%'] < 0]['ROI%'].mean()
    
    # Calculate maximum drawdown
    max_drawdown = (year_trades['ROI%'].cumsum() - year_trades['ROI%'].cumsum().cummax()).min()
    
    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)
    
    # Store the statistics in the DataFrame
    stats_df6.loc[year] = [total_roi, total_trades, win_rate, avg_profit, avg_loss, max_drawdown, roi_dd_ratio]

# Calculate overall statistics
overall_total_roi = stats_df6['Total ROI'].sum()
overall_total_trades = stats_df6['Total Trades'].sum()
overall_win_rate = (pe_sell_tb['ROI%'] > 0).mean() * 100
overall_avg_profit = pe_sell_tb[pe_sell_tb['ROI%'] > 0]['ROI%'].mean()
overall_avg_loss = pe_sell_tb[pe_sell_tb['ROI%'] < 0]['ROI%'].mean()
overall_max_drawdown = (pe_sell_tb['ROI%'].cumsum() - pe_sell_tb['ROI%'].cumsum().cummax()).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df6.loc['Overall'] = [overall_total_roi, overall_total_trades, overall_win_rate, overall_avg_profit, overall_avg_loss, overall_max_drawdown, overall_roi_dd_ratio]
stats_df6

NameError: name 'pe_sell_tb' is not defined

In [134]:
# Final Attempt !
#Positional Sell Side

def execute_sell_side(df):
    portfolio_value = 1000000
    trade_book = []
    in_trade = False
    signal_entry_price = 100000
    signal_initial_sl = 0
    already_signal_exists = False
    is_trailing_active = False

    for i in range(1, len(df)):
        points = 0
        current_candle_open = df.iloc[i]['o']
        current_candle_high = df.iloc[i]['h']
        current_candle_low = df.iloc[i]['l']
        current_candle_close = df.iloc[i]['c']
        current_moving_average_price = df.iloc[i]['MA10']
    
        if not in_trade:
            if df.iloc[i]['Sell_Signal'] == 1:
                if not already_signal_exists:
                    # Fresh Buy Signal
                    signal_entry_price = current_candle_low
                    signal_initial_sl = current_candle_high
                    signal_creation_time = df.iloc[i]['datetime']
                    already_signal_exists = True
                    
                else:
                    if current_candle_open < signal_entry_price:
                        # Gap Down Open, SKIP trade
                        already_signal_exists = False
                        signal_entry_price = 100000
                        signal_initial_sl = 0
                    elif current_candle_low > signal_entry_price:
                        # Better Candle
                        signal_entry_price = current_candle_low
                        signal_initial_sl = current_candle_high
                        signal_creation_time = df.iloc[i]['datetime']
                    
                    elif current_candle_low < signal_entry_price:
                        # Entry Triggered
                        in_trade = True
                        entry_time = df.iloc[i]['datetime']
                        entry_price = signal_entry_price
                        points = 0
            else:
                # Discard Existing Signal
                already_signal_exists = False
                signal_entry_price = 100000
                signal_initial_sl = 0
    
        # else:
        #     trade_entry_price = signal_entry_price
        #     trade_initial_sl = signal_initial_sl
        #     trade_final_sl = signal_initial_sl
    
        #     if not is_trailing_active and current_candle_high < current_moving_average_price:
        #         is_trailing_active = True
    
        #     if not is_trailing_active:
        #         if current_candle_high > trade_initial_sl:
        #             # Initial SL Hit
        #             in_trade = False
        #             points = -1 * (trade_initial_sl - trade_entry_price)
        #             exit_price = trade_initial_sl
        #             exit_time = df.iloc[i]['datetime']
    
        #     else:
        #         trade_final_sl = min(trade_initial_sl, current_moving_average_price)
                
        #         if current_candle_close > trade_final_sl:
        #             # Price Closed below TSL i.e. MA10 , TSL Hit
        #             in_trade = False
        #             points = -1 * (current_candle_close - trade_entry_price)
        #             exit_price = current_candle_close
        #             exit_time = df.iloc[i]['datetime']
        #             is_trailing_active = False

        else:
            trade_entry_price = signal_entry_price
            trade_initial_sl = signal_initial_sl
            trade_final_sl = signal_initial_sl
    
            if not is_trailing_active and current_candle_high < current_moving_average_price:
                is_trailing_active = True
    
            if not is_trailing_active:
                if current_candle_high > trade_initial_sl:
                    # Initial SL Hit
                    in_trade = False
                    points = -1 * (trade_initial_sl - trade_entry_price)
                    exit_price = trade_initial_sl
                    exit_time = df.iloc[i]['datetime']
    
            else:
                trade_final_sl = min(trade_initial_sl, current_moving_average_price)
                
                if current_candle_high > trade_initial_sl:
                    if trade_initial_sl <= current_moving_average_price:
                        # Despite Trailing, Initial SL hit
                        in_trade = False
                        points = -1 * (trade_initial_sl - trade_entry_price)
                        exit_price = trade_initial_sl
                        exit_time = df.iloc[i]['datetime']
                    
                elif current_candle_close > trade_final_sl:
                    # Price Closed below TSL i.e. MA10 , TSL Hit
                    in_trade = False
                    points = -1 * (current_candle_close - trade_entry_price)
                    exit_price = current_candle_close
                    exit_time = df.iloc[i]['datetime']
                    is_trailing_active = False
    
            if points:
                qty = 1000000 * 5 / entry_price
                slippage = 0.0005 * (entry_price + exit_price)
                # slippage = 10
                final_points = points - slippage
                # final_points = points
                
                trade = {
                    'Signal Generated At': signal_creation_time,
                    'Entry Time': entry_time,
                    'Entry Price': entry_price,
                    'Initial SL': trade_initial_sl,
                    'Final SL': trade_final_sl,
                    'Exit Time': exit_time,
                    'Exit Price': exit_price,
                    'Points Captured': points,
                    'After Costs': final_points,
                    'Qty': qty,
                    'ROI%': (final_points * qty /portfolio_value) * 100,
                    'Trade Year': entry_time.year
                }
                trade_book.append(trade)
                points = 0
                in_trade = False
                already_signal_exists = False
                is_trailing_active = False

    trade_book_df = pd.DataFrame(trade_book)
    return trade_book_df
        

In [135]:
tradebook_sell_side = execute_sell_side(signals_df2)
# tradebook_sell_side

In [136]:
stats_df8 = pd.DataFrame(index=range(2015, 2024), columns=['Total ROI', 'Total Trades', 'Win Rate', 'Avg Profit% per Trade', 'Avg Loss% per Trade', 'Max Drawdown', 'ROI/DD Ratio'])

# Iterate over each year
for year in range(2015, 2024):
    # Filter trades for the current year
    year_trades = tradebook_sell_side[(tradebook_sell_side['Trade Year'] == year)]
    
    # Calculate total ROI
    total_roi = year_trades['ROI%'].sum()
    
    # Calculate total number of trades
    total_trades = len(year_trades)
    
    # Calculate win rate
    win_rate = (year_trades['ROI%'] > 0).mean()*100
    
    # Calculate average profit per trade
    avg_profit = year_trades[year_trades['ROI%'] > 0]['ROI%'].mean()
    
    # Calculate average loss per trade
    avg_loss = year_trades[year_trades['ROI%'] < 0]['ROI%'].mean()
    
    # Calculate maximum drawdown
    max_drawdown = (year_trades['ROI%'].cumsum() - year_trades['ROI%'].cumsum().cummax()).min()
    
    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)
    
    # Store the statistics in the DataFrame
    stats_df8.loc[year] = [total_roi, total_trades, win_rate, avg_profit, avg_loss, max_drawdown, roi_dd_ratio]

# Calculate overall statistics
overall_total_roi = stats_df8['Total ROI'].sum()
overall_total_trades = stats_df8['Total Trades'].sum()
overall_win_rate = (tradebook_sell_side['ROI%'] > 0).mean() * 100
overall_avg_profit = tradebook_sell_side[tradebook_sell_side['ROI%'] > 0]['ROI%'].mean()
overall_avg_loss = tradebook_sell_side[tradebook_sell_side['ROI%'] < 0]['ROI%'].mean()
overall_max_drawdown = (tradebook_sell_side['ROI%'].cumsum() - tradebook_sell_side['ROI%'].cumsum().cummax()).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df8.loc['Overall'] = [overall_total_roi, overall_total_trades, overall_win_rate, overall_avg_profit, overall_avg_loss, overall_max_drawdown, overall_roi_dd_ratio]
stats_df8

Total ROI Total Trades   Win Rate Avg Profit% per Trade  \
2015     39.380723           25       44.0              5.858001   
2016     34.766055           42  33.333333              5.748776   
2017     13.795072           39  28.205128              5.227704   
2018    -16.717618           41  29.268293              2.920198   
2019    -12.347144           28  32.142857              3.054106   
2020    -28.536572           33  21.212121             10.180943   
2021     -33.78696           56  23.214286              4.415246   
2022    -42.629453           43  13.953488              5.601132   
2023    -36.883697           49  14.285714              4.204439   
Overall -82.959594        356.0  24.728261              5.040856   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio  
2015              -1.789806   -10.924511     3.604804  
2016              -1.632743   -19.184233      1.81222  
2017               -1.56106   -12.146145     1.135757  
2018              -1.784827    -33.62648    -0.497156  
2019              -2.096531   -20.915602    -0.590332  
2020              -3.838583   -67.363755    -0.423619  
2021              -2.120585   -45.631365    -0.740433  
2022              -2.060439   -45.763942    -0.931507  
2023              -1.578923   -34.735438    -1.061846  
Overall           -2.004705  -191.264915    -0.433742

In [117]:
# 36, 8, 3 -> Sell Side MIDCP

In [1254]:
# tradebook_sell_side.to_csv('MTrend MIDCP Short Final TB.csv')

In [137]:
# TB_LONG = pd.read_csv('../data/MTrend MIDCP Long Final TB.csv')
# TB_SHORT = pd.read_csv('../data/MTrend MIDCP Short Final TB.csv')

TB_LONG = tradebook_buy_side
TB_SHORT = tradebook_sell_side

In [138]:
df1 = pd.DataFrame(TB_LONG)
df2 = pd.DataFrame(TB_SHORT)

In [139]:
combined_df = pd.concat([df1, df2], ignore_index=True)
combined_df_sorted = combined_df.sort_values(by='Entry Time')
combined_df.drop(columns=['Trade Month'], inplace=True)
# combined_df

In [105]:
# df1

In [106]:
# df2

In [107]:
# combined_df.to_csv('MTrend MIDCP B_S Combined Final.csv')

In [140]:
stats_df8 = pd.DataFrame(index=range(2015, 2024), columns=['Total ROI', 'Total Trades', 'Win Rate', 'Avg Profit% per Trade', 'Avg Loss% per Trade', 'Max Drawdown', 'ROI/DD Ratio'])

# Iterate over each year
for year in range(2015, 2024):
    # Filter trades for the current year
    year_trades = combined_df[(combined_df['Trade Year'] == year)]
    
    # Calculate total ROI
    total_roi = year_trades['ROI%'].sum()
    
    # Calculate total number of trades
    total_trades = len(year_trades)
    
    # Calculate win rate
    win_rate = (year_trades['ROI%'] > 0).mean()*100
    
    # Calculate average profit per trade
    avg_profit = year_trades[year_trades['ROI%'] > 0]['ROI%'].mean()
    
    # Calculate average loss per trade
    avg_loss = year_trades[year_trades['ROI%'] < 0]['ROI%'].mean()
    
    # Calculate maximum drawdown
    max_drawdown = (year_trades['ROI%'].cumsum() - year_trades['ROI%'].cumsum().cummax()).min()
    
    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)
    
    # Store the statistics in the DataFrame
    stats_df8.loc[year] = [total_roi, total_trades, win_rate, avg_profit, avg_loss, max_drawdown, roi_dd_ratio]

# Calculate overall statistics
overall_total_roi = stats_df8['Total ROI'].sum()
overall_total_trades = stats_df8['Total Trades'].sum()
overall_win_rate = (combined_df['ROI%'] > 0).mean() * 100
overall_avg_profit = combined_df[combined_df['ROI%'] > 0]['ROI%'].mean()
overall_avg_loss = combined_df[combined_df['ROI%'] < 0]['ROI%'].mean()
overall_max_drawdown = (combined_df['ROI%'].cumsum() - combined_df['ROI%'].cumsum().cummax()).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df8.loc['Overall'] = [overall_total_roi, overall_total_trades, overall_win_rate, overall_avg_profit, overall_avg_loss, overall_max_drawdown, overall_roi_dd_ratio]
stats_df8

Total ROI Total Trades   Win Rate Avg Profit% per Trade  \
2015      67.432794           60       40.0              5.633633   
2016     107.667526           86  34.883721              7.150744   
2017      16.819476           90  27.777778              4.789181   
2018       3.650893           85  32.941176              3.601852   
2019      85.438498           79  34.177215              6.954959   
2020      48.237041           89  25.842697             10.578576   
2021     -25.222436           94  28.723404              3.971204   
2022     -33.505996           97  20.618557              6.292143   
2023      -37.93839           96      18.75              5.014645   
Overall  232.579406        776.0  28.211587              6.026285   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio  
2015              -1.882622   -31.206793     2.160837  
2016              -1.908121   -24.291792      4.43226  
2017              -1.583231   -22.109752     0.760727  
2018               -1.70528    -40.09759      0.09105  
2019               -1.96818   -20.915602     4.084917  
2020              -2.955609   -67.363755     0.716068  
2021               -1.97679   -45.631365    -0.552743  
2022              -2.069466   -67.639984    -0.495358  
2023              -1.643615   -56.591132    -0.670395  
Overall           -1.956166  -191.264915     1.216007

In [87]:
# Combined Tradebook Gold Buy+Sell Both Best Variations